In [1]:
!pip install einops
!pip install captum
!pip install shap

  Obtaining dependency information for einops from https://files.pythonhosted.org/packages/29/0b/2d1c0ebfd092e25935b86509a9a817159212d82aa43d7fb07eca4eeff2c2/einops-0.7.0-py3-none-any.whl.metadata
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.6/44.6 kB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 21.1 MB/s eta 0:00:00a 0:00:01


In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import random
import torch
import copy

import numpy as np

from tqdm.notebook import tqdm

from transformers import AutoModelForCausalLM, AutoTokenizer, AutoConfig

from captum.attr import IntegratedGradients, LayerIntegratedGradients
from captum.attr import visualization as viz

import shap

/opt/conda/lib/python3.10/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.24.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [4]:
torch.manual_seed(12345)
np.random.seed(12345)

In [5]:
device = "cuda"
torch.set_default_device(device)

In [6]:
model = AutoModelForCausalLM.from_pretrained("microsoft/phi-1_5", trust_remote_code=True)
tokenizer = AutoTokenizer.from_pretrained("microsoft/phi-1_5", trust_remote_code=True, use_fast=True)
config = AutoConfig.from_pretrained("microsoft/phi-1_5", trust_remote_code=True)

model.eval()
model.zero_grad()

A new version of the following files was downloaded from https://huggingface.co/microsoft/phi-1_5:
- configuration_phi.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


A new version of the following files was downloaded from https://huggingface.co/microsoft/phi-1_5:
- modeling_phi.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


In [7]:
test_query = ["How are you today?"]
animal_queries = [
    "What sound does the dog make?\n\nAnswer:",
    "What is a dog?\n\nAnswer:",
    "What sound does the cat make?\n\nAnswer:",
    "What is a cat?\n\nAnswer:",
    "What is a the difference between a cat and a dog?\n\nAnswer:",
]
city_queries = [
    "Where is London?\n\nAnswer:",
    "Where is Paris?\n\nAnswer:",
    "What is the captial of the United Kingdom?\n\nAnswer:",
    "What is the capital of France?\n\nAnswer:",
]

In [8]:
def swap_emb_weights(emb_weights, a_indexes, b_indexes):
    a_weights = emb_weights[a_indexes]
    b_weights = emb_weights[b_indexes]

    swap_weights = emb_weights.clone()
    swap_weights[a_indexes] = b_weights
    swap_weights[b_indexes] = a_weights
    return swap_weights

In [9]:
try:
    emb_weights
except NameError:
    emb_weights = model.get_input_embeddings().weight
try:
    original_generate
except NameError:
    original_generate = model.generate

word_inputs = tokenizer([" dog", " cat"], return_tensors="pt", return_attention_mask=False)
dog_indexes = word_inputs["input_ids"][0]
cat_indexes = word_inputs["input_ids"][1]

swap_weights = swap_emb_weights(emb_weights, dog_indexes, cat_indexes)

## Captum

In [10]:
def llm_captum(model, queries, baseline_query = " ", max_length=20):
    # Define forward wrapper function to extrapolate logits values
    def custom_forward(inputs):
        out = model.forward(inputs)
        logits = out.logits
        return logits.max(1).values
    
    # Create a LayerIntegratedGradients wrapper for the model
    lig = LayerIntegratedGradients(custom_forward, model.get_input_embeddings())
    
    # Define a reference sequence of token ids from a baseline query
    ref_input_ids = None
    if baseline_query:
        ref_input_ids = tokenizer(baseline_query, return_tensors="pt", return_attention_mask=False).input_ids
    
    vis = []
    # Iterate over all queries, saving attributions information for each one
    for query in tqdm(queries):
        # Elaborate full model output while 
        inputs = tokenizer(query, return_tensors="pt", return_attention_mask=False)
        out = model.generate(**inputs, max_length=max_length)
        prompt_n = inputs.input_ids.squeeze().size()[0]
        output_n = out.squeeze().size()[0]
    
        records = []
        # Gather attributions information for each token of the modedl output for a given query
        for i in tqdm(range(prompt_n, output_n)):
            attributions, delta = lig.attribute(
                inputs=out[:i],
                baselines=ref_input_ids,
                return_convergence_delta=True,
                target=out[0][i]
            )
            records.append(viz.VisualizationDataRecord(
                attributions.sum(dim=-1).squeeze(0),
                torch.as_tensor(0),
                tokenizer.decode(out[0][i]),
                0,
                0,
                attributions.sum(),       
                tokenizer.convert_ids_to_tokens(out[0][:i].tolist()),
                delta
            ))
        vis.append(records)
    
    return vis

### Testing different baselines

In [11]:
model.get_input_embeddings().weight = torch.nn.Parameter(emb_weights)
# Whitespace
vis = llm_captum(model, [animal_queries[0]], max_length=20)
# No baseline
vis += llm_captum(model, [animal_queries[0]], None, max_length=20)
# \n
vis += llm_captum(model, [animal_queries[0]], "\n", max_length=20)
# \n\n
vis += llm_captum(model, [animal_queries[0]], "\n\n", max_length=20)
# end of text
vis += llm_captum(model, [animal_queries[0]], "<|endoftext|>", max_length=20)

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

In [12]:
for v in vis:
    _ = viz.visualize_text(v)

### Testing animal queries

In [13]:
# Without swap
model.get_input_embeddings().weight = torch.nn.Parameter(emb_weights)
vis = llm_captum(model, animal_queries, max_length=20)

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

In [14]:
for v in vis:
    _ = viz.visualize_text(v)

In [15]:
# With swap
model.get_input_embeddings().weight = torch.nn.Parameter(swap_weights)
vis = llm_captum(model, animal_queries, max_length=20)

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

In [16]:
for v in vis:
    _ = viz.visualize_text(v)

### Deswapped animal queries

In [17]:
def deswap_forward_wrapper(f, model, reference_weights):
    def inner(*args, **kwargs):
        result = f(*args, **kwargs)
        if model.deswap_flag:
            model.get_input_embeddings().weight = torch.nn.Parameter(reference_weights)
            model.deswap_flag = False
        return result
    return inner
    
def deswap_generate_wrapper(f, model, swap_weights=None):
    def inner(*args, **kwargs):
        
        reference_weights = model.get_input_embeddings().weight
        reference_forward = model.forward
        model.forward = deswap_forward_wrapper(model.forward, model, reference_weights)
        if swap_weights is not None:
            model.get_input_embeddings().weight = torch.nn.Parameter(swap_weights)
        model.deswap_flag = True
        
        result = f(*args, **kwargs)
        
        model.forward = reference_forward
        model.get_input_embeddings().weight = torch.nn.Parameter(reference_weights)
        model.deswap_flag = True
        
        return result
    
    return inner

In [18]:
model.generate = deswap_generate_wrapper(original_generate, model, swap_weights)
vis = llm_captum(model, animal_queries, max_length=20)
model.generate = original_generate

  0%|          | 0/5 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/9 [00:00<?, ?it/s]

  0%|          | 0/11 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

In [19]:
for v in vis:
    _ = viz.visualize_text(v)

## Shap

### GPT2 Creation

In [20]:
tokenizer_gpt = AutoTokenizer.from_pretrained("gpt2", use_fast=True)
model_gpt = AutoModelForCausalLM.from_pretrained("gpt2")

# set model decoder to true
model_gpt.config.is_decoder = True
# set text-generation params under task_specific_params
model_gpt.config.task_specific_params["text-generation"] = {
    "do_sample": True,
    "max_length": 1,
    "temperature": 0.7,
    "top_k": 50,
    "no_repeat_ngram_size": 2,
}

model_gpt.eval()
model_gpt.zero_grad()

### Evaluation

In [21]:
def shap_explain(explainer, queries):
    v = []
    for q in queries:
        shap_values = explainer([q])
        v.append(shap_values)
        shap.plots.text(shap_values)
    return v

In [22]:
explainer = shap.Explainer(model_gpt, tokenizer_gpt)
_ = shap_explain(explainer, animal_queries)

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Using the model-agnostic default `max_length` (=20) to control the generation length. We recommend setting `max_new_tokens` to control the maximum length of the generation.


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
